In [1]:
import pandas as pd
import json
import os
import shutil
import tensorflow as tf
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.utils import image_dataset_from_directory
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense
from tensorflow.keras.callbacks import Callback

In [2]:
def create_dataframe(annotations_path):
    with open(annotations_path, 'r') as file:
        data = json.load(file)

    images = pd.DataFrame(data['images']).rename(columns={'id': 'image_id'})[['image_id', 'file_name']]

    categories = pd.DataFrame(data['categories'])[['id', 'name']]
    categories.rename(columns={'id': 'category_id'}, inplace=True)

    usecols = ['image_id', 'category_id']
    annotations = pd.DataFrame(data['annotations'])[usecols]

    dataframe = annotations.merge(categories, on='category_id').merge(images, on='image_id')[['file_name', 'name']]
    
    return dataframe

In [3]:
def copy_images_to_destination(base_dir, dataframe, split):
    images_dir = os.path.join(base_dir, 'images')

    for index, row in dataframe.iterrows():
        file_name = row['file_name']
        file_class = row['name']

        dest_dir = os.path.join(split, file_class)
        os.makedirs(dest_dir, exist_ok=True)

        source_path = os.path.join(images_dir, file_name)
        destination_path = os.path.join(dest_dir, file_name)

        shutil.copyfile(source_path, destination_path)

    print("Done copying images.")

In [4]:
train_df = create_dataframe('train/annotations.json')
train_df

file_name             name
0      131094.jpg      soft-cheese
1      131094.jpg          ham-raw
2      131094.jpg      hard-cheese
3      131094.jpg  bread-wholemeal
4      131094.jpg   cottage-cheese
...           ...              ...
76486  117029.jpg      damson-plum
76487  117524.jpg      damson-plum
76488  117849.jpg      damson-plum
76489  123468.jpg      damson-plum
76490  095795.jpg       bean-seeds

[76491 rows x 2 columns]

In [5]:
splits = ['train', 'val']

for split in splits:
    root = f'{split}'

    for index, row in train_df.iterrows():
        directory_name = row['name']
        directory_path = os.path.join(root, directory_name)

        if not os.path.exists(directory_path):
            os.makedirs(directory_path)

In [6]:
val_df = create_dataframe('val/annotations.json')
val_df

file_name                    name
0     149022.jpg  espresso-with-caffeine
1     149022.jpg          dark-chocolate
2     167905.jpg  espresso-with-caffeine
3     121313.jpg  espresso-with-caffeine
4     153429.jpg  espresso-with-caffeine
...          ...                     ...
1825  144675.jpg                oat-milk
1826  103273.jpg             soup-potato
1827  159922.jpg             red-cabbage
1828  011275.jpg     pasta-in-conch-form
1829  166537.jpg               chocolate

[1830 rows x 2 columns]

In [7]:
base_dir = 'train'
dataframe = train_df
copy_images_to_destination(base_dir, dataframe, 'train')

Done copying images.


In [8]:
base_dir = 'val'
dataframe = val_df
copy_images_to_destination(base_dir, dataframe, 'val')

Done copying images.


In [2]:
train = image_dataset_from_directory(
    directory='train',
    label_mode='categorical',
    batch_size=32,
    image_size=(299, 299)
)

val = image_dataset_from_directory(
    directory='val',
    label_mode='categorical',
    batch_size=32,
    image_size=(299, 299)
)

Found 70397 files belonging to 498 classes.
Found 1799 files belonging to 498 classes.


In [3]:
train_datagen = ImageDataGenerator(
    rescale=1./255,
    shear_range=0.2,
    zoom_range=0.2,
    horizontal_flip=True
)

val_datagen = ImageDataGenerator(rescale=1./255)

In [4]:
class MyCallback(Callback):
    def on_epoch_end(self, epoch, logs={}):
        if logs.get('val_categorical_accuracy') >= 0.81:
            print('Validation accuracy reached 81%. Stopping training.')

In [5]:
model = Sequential()
model.add(Conv2D(32, (3, 3), activation='relu', input_shape=(299, 299, 3)))
model.add(MaxPooling2D((2, 2)))
model.add(Conv2D(64, (3, 3), activation='relu'))
model.add(MaxPooling2D((2, 2)))
model.add(Conv2D(128, (3, 3), activation='relu'))
model.add(MaxPooling2D((2, 2)))
model.add(Flatten())
model.add(Dense(128, activation='relu'))
model.add(Dense(498, activation='softmax'))

model.summary()

model.compile(optimizer=tf.keras.optimizers.Adam(),
              loss=tf.keras.losses.CategoricalCrossentropy(),
              metrics=[tf.keras.metrics.CategoricalAccuracy()])

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 297, 297, 32)      896       
                                                                 
 max_pooling2d (MaxPooling2D  (None, 148, 148, 32)     0         
 )                                                               
                                                                 
 conv2d_1 (Conv2D)           (None, 146, 146, 64)      18496     
                                                                 
 max_pooling2d_1 (MaxPooling  (None, 73, 73, 64)       0         
 2D)                                                             
                                                                 
 conv2d_2 (Conv2D)           (None, 71, 71, 128)       73856     
                                                                 
 max_pooling2d_2 (MaxPooling  (None, 35, 35, 128)      0

In [6]:
callback = MyCallback()
history = model.fit(train, epochs=32, validation_data=val, callbacks=[callback])

Epoch 1/32
2200/2200 [==============================] - 291s 130ms/step - loss: 6.9090 - categorical_accuracy: 0.0398 - val_loss: 5.5961 - val_categorical_accuracy: 0.0411
Epoch 2/32
2200/2200 [==============================] - 279s 127ms/step - loss: 5.4654 - categorical_accuracy: 0.0420 - val_loss: 5.5951 - val_categorical_accuracy: 0.0417
Epoch 3/32
2200/2200 [==============================] - 276s 125ms/step - loss: 5.4428 - categorical_accuracy: 0.0449 - val_loss: 5.6058 - val_categorical_accuracy: 0.0417
Epoch 4/32
2200/2200 [==============================] - 285s 130ms/step - loss: 5.3952 - categorical_accuracy: 0.0528 - val_loss: 5.6658 - val_categorical_accuracy: 0.0411
Epoch 5/32
2200/2200 [==============================] - 282s 128ms/step - loss: 5.3362 - categorical_accuracy: 0.0630 - val_loss: 5.7703 - val_categorical_accuracy: 0.0406
Epoch 6/32
2200/2200 [==============================] - 326s 148ms/step - loss: 5.2673 - categorical_accuracy: 0.0755 - val_loss: 5.7254 - v